# Task4

Index_X = FSR_for_force, FSR_for_coord

Index_y = force, x_coord, y_coord

Data = Splited by Subject

## Run result

https://wandb.ai/seokjin/FSR-prediction/groups/FSR_Trainable_2023-07-05_12-59-09/workspace?workspace=user-seokjin

## Experiment id

FSR_Trainable_2023-07-05_12-59-09

In [1]:
def define_searchspace(trial):
    model = trial.suggest_categorical('model', ['fsr_model.LSTM', 'fsr_model.CNN_LSTM', 'fsr_model.ANN'])
    if model == 'fsr_model.LSTM':
        trial.suggest_categorical('model_args/hidden_size', [8, 16, 32, 64, 128])
        trial.suggest_int('model_args/num_layer', 1, 8)
    elif model == 'fsr_model.CNN_LSTM':
        trial.suggest_categorical('model_args/cnn_hidden_size', [8, 16, 32, 64, 128])
        trial.suggest_categorical('model_args/lstm_hidden_size', [8, 16, 32, 64, 128])
        trial.suggest_int('model_args/cnn_num_layer', 1, 8)
        trial.suggest_int('model_args/lstm_num_layer', 1, 8)
    elif model == 'fsr_model.ANN':
        trial.suggest_categorical('model_args/hidden_size', [8, 16, 32, 64, 128])
        trial.suggest_int('model_args/num_layer', 1, 8)
    trial.suggest_categorical('criterion', ['torch.nn.MSELoss'])
    trial.suggest_categorical('optimizer', [
        'torch.optim.Adam',
        'torch.optim.NAdam',
        'torch.optim.Adagrad',
        'torch.optim.RAdam',
        'torch.optim.SGD',
    ])
    trial.suggest_float('optimizer_args/lr', 1e-5, 1e-1, log=True)
    imputer = trial.suggest_categorical('imputer', ['sklearn.impute.SimpleImputer'])
    if imputer == 'sklearn.impute.SimpleImputer':
        trial.suggest_categorical('imputer_args/strategy', [
            'mean',
            'median',
        ])
    trial.suggest_categorical('scaler', [ 
        'sklearn.preprocessing.StandardScaler',
        'sklearn.preprocessing.MinMaxScaler',
        'sklearn.preprocessing.RobustScaler',
    ])
    return {
        'index_X': ['FSR_for_force', 'FSR_for_coord'],
        'index_y': ['force', 'x_coord', 'y_coord'],
        'data_loader': 'fsr_data.get_index_splited_by_subject'
    }

In [2]:
import ray.tune
import ray.air
import ray.air.integrations.wandb
import ray.tune.schedulers
from fsr_trainable import FSR_Trainable
import ray.tune.search
import ray.tune.search.optuna

tuner = ray.tune.Tuner(
    trainable=ray.tune.with_resources(
        FSR_Trainable, {'cpu':2},
    ),
    tune_config=ray.tune.TuneConfig(
        num_samples=1000,
        scheduler=ray.tune.schedulers.ASHAScheduler(
            max_t=100,
            grace_period=1,
            reduction_factor=2,
            brackets=1,
            metric='rmse',
            mode='min',
        ),
        search_alg=ray.tune.search.optuna.OptunaSearch(
            space=define_searchspace,
            metric='rmse',
            mode='min',
        ),
    ), 
    run_config=ray.air.RunConfig(
        callbacks=[
            ray.air.integrations.wandb.WandbLoggerCallback(project='FSR-prediction'),
        ],
        checkpoint_config=ray.air.CheckpointConfig(
            num_to_keep=3,
            checkpoint_score_attribute='rmse',
            checkpoint_score_order='min',
            checkpoint_frequency=5,
            checkpoint_at_end=True,
        ),
    ), 
)

[I 2023-07-05 21:30:17,633] A new study created in memory with name: optuna


In [3]:
results = tuner.fit()

2023-07-05 12:59:12,225	INFO worker.py:1627 -- Started a local Ray instance. View the dashboard at 127.0.0.1:8265 
2023-07-05 12:59:13,560	INFO tune.py:226 -- Initializing Ray automatically. For cluster usage or custom Ray initialization, call `ray.init(...)` before `Tuner(...)`.


2023-07-05 12:59:13,621	INFO wandb.py:320 -- Already logged into W&B.


(_WandbLoggingActor pid=704835) wandb: Currently logged in as: seokjin. Use `wandb login --relogin` to force relogin
(_WandbLoggingActor pid=704835) wandb: Tracking run with wandb version 0.15.4
(_WandbLoggingActor pid=704835) wandb: Run data is saved locally in /home/seokj/ray_results/FSR_Trainable_2023-07-05_12-59-09/FSR_Trainable_80da3f67_1_criterion=torch_nn_MSELoss,data_loader=fsr_data_get_index_splited_by_subject,imputer=sklearn_impute_Simpl_2023-07-05_12-59-13/wandb/run-20230705_125924-80da3f67
(_WandbLoggingActor pid=704835) wandb: Run `wandb offline` to turn off syncing.
(_WandbLoggingActor pid=704835) wandb: Syncing run FSR_Trainable_80da3f67
(_WandbLoggingActor pid=704835) wandb: ⭐️ View project at https://wandb.ai/seokjin/FSR-prediction
(_WandbLoggingActor pid=704835) wandb: 🚀 View run at https://wandb.ai/seokjin/FSR-prediction/runs/80da3f67
(_WandbLoggingActor pid=705009) wandb: Currently logged in as: seokjin. Use `wandb login --relogin` to force relogin
(_WandbLoggingAct

2023-07-05 14:48:07,712	WARNING util.py:315 -- The `callbacks.on_trial_result` operation took 3.876 s, which may be a performance bottleneck.
2023-07-05 14:48:07,718	WARNING util.py:315 -- The `process_trial_result` operation took 3.883 s, which may be a performance bottleneck.
2023-07-05 14:48:07,720	WARNING util.py:315 -- Processing trial results took 3.885 s, which may be a performance bottleneck. Please consider reporting results less frequently to Ray Tune.
2023-07-05 14:48:07,722	WARNING util.py:315 -- The `process_trial_result` operation took 3.886 s, which may be a performance bottleneck.


In [4]:
results = tuner.restore(
    path='/home/seokj/ray_results/FSR_Trainable_2023-07-05_12-59-09',
    trainable=FSR_Trainable,
).fit()

2023-07-05 21:32:18,504	INFO experiment_analysis.py:966 -- No trial data passed in during `ExperimentAnalysis` initialization -- you are most likely loading the experiment after it has completed.
Loading trial data from the experiment checkpoint file. This may result in loading some stale information, since checkpointing is periodic.


2023-07-05 21:32:21,563	INFO experiment_state.py:435 -- A local experiment checkpoint was found and will be used to restore the previous experiment state.
2023-07-05 21:32:21,601	WARNING trial_runner.py:418 -- Attempting to resume experiment from /home/seokj/ray_results/FSR_Trainable_2023-07-05_12-59-09. This will ignore any new changes to the specification.
2023-07-05 21:32:21,602	INFO trial_runner.py:422 -- Using the newest experiment state file found within the experiment directory: experiment_state-2023-07-05_21-30-25.json
2023-07-05 21:32:24,958	INFO wandb.py:320 -- Already logged into W&B.
2023-07-05 21:32:27,368	INFO tune.py:1111 -- Total run time: 5.85 seconds (0.00 seconds for the tuning loop).


(raylet) [2023-07-05 21:56:23,434 E 75614 75614] (raylet) node_manager.cc:3069: 1 Workers (tasks / actors) killed due to memory pressure (OOM), 0 Workers crashed due to other reasons at node (ID: 88697f47488e3eef3ef0885f2246dd05ce5ee6ed5dd6e9b1280dd318, IP: 172.26.215.93) over the last time period. To see more information about the Workers killed on this node, use `ray logs raylet.out -ip 172.26.215.93`
(raylet) 
(raylet) Refer to the documentation on how to address the out of memory issue: https://docs.ray.io/en/latest/ray-core/scheduling/ray-oom-prevention.html. Consider provisioning more memory on this node or reducing task parallelism by requesting more CPUs per task. To adjust the kill threshold, set the environment variable `RAY_memory_usage_threshold` when starting Ray. To disable worker killing, set the environment variable `RAY_memory_monitor_refresh_ms` to zero.
